In [660]:
from os.path import join
import pandas.io.sql as psql
import sqlite3 as sql
from bokeh.sampledata.movies_data import movie_path

conn = sql.connect(movie_path)
dirname = os.getcwd()
query = open(join(dirname, 'query.sql')).read()
movies = psql.read_sql(query, conn)
movies.columns

Index(['ID', 'imdbID', 'Title', 'Year', 'mpaaRating', 'Runtime', 'Genre',
       'Released', 'Director', 'Writer', 'Cast', 'imdbRating', 'imdbVotes',
       'Language', 'Country', 'Oscars', 'numericRating', 'Meter', 'Reviews',
       'Fresh', 'Rotten', 'userMeter', 'userRating', 'userReviews',
       'BoxOffice', 'Production'],
      dtype='object')

In [661]:
import numpy as np

movies['color'] = np.where(movies['Oscars'] > 0, 'orange', 'grey')
movies['alpha'] = np.where(movies['Oscars'] > 0, 0.9, 0.25)
movies['Director'].fillna('', inplace = True)
movies['Cast'].fillna('', inplace = True)
movies['Writer'].fillna('', inplace = True)
movies.fillna(0, inplace = True)
movies['revenue'] = movies.BoxOffice.apply(lambda x: '{:,d}'.format(int(x)))

with open(join(dirname, 'razzies-clean.csv')) as f:
    razzies = f.read().splitlines()
movies.loc[movies.imdbID.isin(razzies), 'color'] = 'purple'
movies.loc[movies.imdbID.isin(razzies), 'alpha'] = 0.9

axis_map = {
    'Tomato Meter': 'Meter',
    'Number Rating': 'numericRating',
    'Number of Reviews': 'Reviews',
    'Box Office (dollars)': 'BoxOffice',
    'Lenght (minutes)': 'Runtime',
    'Year': 'Year'
}
genreOption = open(join(dirname, 'genres.txt')).read().splitlines()

In [662]:
from bokeh.models.widgets import Slider, Div, Select, TextInput
from bokeh.layouts import layout, widgetbox
from bokeh.plotting import Figure, show, output_notebook
from bokeh.models import ColumnDataSource, LinearAxis

#creat all widgets
div = Div(text = open(join(dirname, 'description.html')).read(), width = 800)
sliderReview = Slider(start = 10, end = 300, value = 80, step = 10, title = 'Minimum number of reviews')
sliderBoxOffice = Slider(start = 0, end = 800, value = 0, step = 1, title = 'Dollars at Box Office (millions)')
selectGenre = Select(title = 'Genre', value = 'All', options = genreOption)
sliderYearRelease = Slider(start = 1940, end = 2014, value = 1970, step = 1, title = 'Year released')
sliderEndYearRelease = Slider(start = 1940, end = 2014, value = 2014, step = 1, title = 'End Year released')
sliderMinimumOscarWin = Slider(start = 0, end = 4, value = 0, step = 1, title = 'Minimum number of Oscar wins')
textinputDirector = TextInput(title = 'Director name contains')
textinputCast = TextInput(title = 'Cast names contains')
selectXaxis = Select(title = 'X Axis', value = 'Tomato Meter', options = list(axis_map.keys()))
selectYaxis = Select(title = 'Y Axis', value = 'Number of Reviews', options = list(axis_map.keys()))
control = [sliderReview, sliderBoxOffice, selectGenre, sliderYearRelease, sliderEndYearRelease,
           sliderMinimumOscarWin, textinputDirector, textinputCast, selectXaxis, selectYaxis]
inputs = widgetbox(*control, sizing_mode = 'fixed')

#create source
source1 = ColumnDataSource(movies)
source = ColumnDataSource(dict(x = [], y = [], title = [], year = [], revenue = [], _color = [], _alpha = []))

#create figure
TOOLTIPS = [
    ('Title', '@title'),
    ('Year', '@year'),
    ('$', '@revenue')
]
p = Figure(width = 700, height = 600, toolbar_location = None, tooltips = TOOLTIPS)
p.circle(x = 'x', y = 'y', color = '_color', alpha = '_alpha', size = 7, source = source)
#creat layout
l = layout([[div], [inputs, p]])
ax = LinearAxis(axis_label = 'haha')

In [663]:
def select_movies():
    minimumNumberofReviews = sliderReview.value
    boxOffice = sliderBoxOffice.value
    valueGenre = selectGenre.value
    yearRealised = sliderYearRelease.value
    yearEndRealised = sliderEndYearRelease.value
    minimumOscarWins = sliderMinimumOscarWin.value
    director = textinputDirector.value
    cast = textinputCast.value
    df = movies.loc[movies.Reviews >= minimumNumberofReviews]
    df = df.loc[df.BoxOffice >= boxOffice]
    if (valueGenre != 'All'):
        df = df.loc[df.Genre.str.contains(valueGenre) == True]
    df = df.loc[(df.Year >= yearRealised) & (df.Year <= yearEndRealised)]
    df = df.loc[df.Oscars >= minimumOscarWins]
    if (director != ''):
        df = df.loc[df.Director.str.contains(director) == True]
    if (cast != ''):
        df = df.loc[df.Cast.str.contains(cast) == True]
    return df

df = select_movies()
df = df.reset_index(drop = True)
for i in range(0, df.shape[0] ):
    source.data['x'].append(df.loc[i]['Meter'])
    source.data['y'].append(df.loc[i]['Reviews'])
    source.data['_color'].append(df.loc[i]['color'])
    source.data['_alpha'].append(df.loc[i]['alpha'])
    source.data['title'].append(df.loc[i]['Title'])
    source.data['year'].append(df.loc[i]['Year'])
    source.data['revenue'].append(df.loc[i]['revenue'])
p.title.text = "%d movies selected" % len(source.data['x'])
p.xaxis.axis_label = selectXaxis.value
p.yaxis.axis_label = selectYaxis.value


In [664]:
v1 = sliderReview.value
v2 = sliderBoxOffice.value
v3 = selectGenre.value
v4 = sliderYearRelease.value
v5 = sliderEndYearRelease.value
v6 = sliderMinimumOscarWin.value
v7 = textinputDirector.value
v8 = textinputCast.value
x_axis = axis_map[selectXaxis.value]
y_axis = axis_map[selectYaxis.value]
valueSource = ColumnDataSource(dict(v1 = [v1], v2 = [v2], v3 = [v3], v4  =[v4],
                                    v5 = [v5], v6 = [v6], v7 = [v7], v8 = [v8],
                                    x_axis = [x_axis], y_axis = [y_axis]))

In [665]:

callbackAll = CustomJS(args = dict(source = source, source1 = source1, 
                                   valueSource = valueSource, axis_map = axis_map, p = p, 
                                   xaxis = p.xaxis[0], yaxis = p.yaxis[0]), code = """
    var data = source.data
    var data1 = source1.data
    var x = data['x']
    var y = data['y']
    var _color = data['_color']
    var _alpha = data['_alpha']
    var title = data['title']
    var year = data['year']
    var revenue = data['revenue']
    var dv1 = data1['Reviews']
    var dv2 = data1['BoxOffice']
    var dv3 = data1['Genre']
    var dv4 = data1['Year']
    var dv6 = data1['Oscars']
    var dv7 = data1['Director']
    var dv8 = data1['Cast']
    var v1 = valueSource.data['v1']
    var v2 = valueSource.data['v2']
    var v3 = valueSource.data['v3']
    var v4 = valueSource.data['v4']
    var v5 = valueSource.data['v5']
    var v6 = valueSource.data['v6']
    var v7 = valueSource.data['v7']
    var v8 = valueSource.data['v8']
    var x_axis = valueSource.data['x_axis']
    var y_axis = valueSource.data['y_axis']
    x.splice(0, x.length)
    y.splice(0, y.length)
    _color.splice(0, _color.length)
    _alpha.splice(0, _alpha.length)
    title.splice(0, title.length)
    year.splice(0, year.length)
    revenue.splice(0, revenue.length)
    len = data1['Reviews'].length
    if (cb_obj.title == 'Minimum number of reviews')
        v1[0] = cb_obj.value
    if (cb_obj.title == 'Dollars at Box Office (millions)')
        v2[0] = cb_obj.value
    var tmpV2 = v2[0] * 1000000
    if (cb_obj.title == 'Genre')
        v3[0] = cb_obj.value
    if (cb_obj.title == 'Year released')
        v4[0] = cb_obj.value
    if (cb_obj.title == 'End Year released')
        v5[0] = cb_obj.value
    if (cb_obj.title == 'Minimum number of Oscar wins')
        v6[0] = cb_obj.value
    if (cb_obj.title == 'Director name contains')
        v7[0] = cb_obj.value
    if (cb_obj.title == 'Cast names contains')
        v8[0] = cb_obj.value
    if (cb_obj.title == 'X Axis')
    {
        x_axis[0] = axis_map[cb_obj.value]  
        xaxis.axis_label = cb_obj.value
    }
    if (cb_obj.title == 'Y Axis')
    {
        y_axis[0] = axis_map[cb_obj.value] 
        yaxis.axis_label = cb_obj.value
    }
    for (var i = 0; i < len; i++)
    {
        if (dv1[i] < v1[0] || dv2[i] < tmpV2 || dv4[i] < v4[0] || dv4[i] > v5[0] || dv6[i] < v6[0]) continue;
        if (v3[0] != 'All'){
            if (!dv3[i].includes(v3[0])) continue;
        }
        if (v7[0] != ''){
            if (!dv7[i].includes(v7[0])) continue;
        }
        if (v8[0] != ''){
            if (!dv8[i].includes(v8[0])) continue;
        }
        x.push(data1[x_axis[0]][i])
        y.push(data1[y_axis[0]][i])
        _color.push(data1['color'][i])
        _alpha.push(data1['alpha'][i])
        title.push(data1['Title'][i])
        year.push(data1['Year'][i])
        revenue.push(data1['revenue'][i])
        
    }
    p.title.text = x.length.toString() + ' movies selected'
    source.change.emit()
    valueSource.change.emit()
""")

In [666]:
output_notebook()
sliderReview.js_on_change('value', callbackAll)
sliderBoxOffice.js_on_change('value', callbackAll)
selectGenre.js_on_change('value', callbackAll)
sliderYearRelease.js_on_change('value', callbackAll)
sliderEndYearRelease.js_on_change('value', callbackAll)
sliderMinimumOscarWin.js_on_change('value', callbackAll)
textinputDirector.js_on_change('value', callbackAll)
textinputCast.js_on_change('value', callbackAll)
selectXaxis.js_on_change('value', callbackAll)
selectYaxis.js_on_change('value', callbackAll)
show(l)